In [16]:
import pandas as pd
import re
import numpy as np

In [17]:
df = pd.read_csv("us_cities_states_counties.csv")
df.head(50)

City State short   State full     County  \
0   Holtsville          NY     New York    SUFFOLK   
1   Holtsville          NY     New York    SUFFOLK   
2     Adjuntas          PR  Puerto Rico   ADJUNTAS   
3     Adjuntas          PR  Puerto Rico   ADJUNTAS   
4     Adjuntas          PR  Puerto Rico   ADJUNTAS   
5     Adjuntas          PR  Puerto Rico   ADJUNTAS   
6       Aguada          PR  Puerto Rico     AGUADA   
7       Aguada          PR  Puerto Rico     AGUADA   
8       Aguada          PR  Puerto Rico     AGUADA   
9       Aguada          PR  Puerto Rico     AGUADA   
10      Aguada          PR  Puerto Rico     AGUADA   
11      Aguada          PR  Puerto Rico     AGUADA   
12   Aguadilla          PR  Puerto Rico  AGUADILLA   
13   Aguadilla          PR  Puerto Rico  AGUADILLA   
14   Aguadilla          PR  Puerto Rico  AGUADILLA   
15   Aguadilla          PR  Puerto Rico  AGUADILLA   
16   Aguadilla          PR  Puerto Rico  AGUADILLA   
17   Aguadilla          PR  Puerto Rico  AGUADILLA   
18   Aguadilla          PR  Puerto Rico  AGUADILLA   
19   Aguadilla          PR  Puerto Rico  AGUADILLA   
20   Aguadilla          PR  Puerto Rico  AGUADILLA   
21   Aguadilla          PR  Puerto Rico  AGUADILLA   
22   Aguadilla          PR  Puerto Rico  AGUADILLA   
23   Aguadilla          PR  Puerto Rico  AGUADILLA   
24   Aguadilla          PR  Puerto Rico  AGUADILLA   
25   Aguadilla          PR  Puerto Rico  AGUADILLA   
26   Aguadilla          PR  Puerto Rico  AGUADILLA   
27   Aguadilla          PR  Puerto Rico  AGUADILLA   
28   Aguadilla          PR  Puerto Rico  AGUADILLA   
29   Aguadilla          PR  Puerto Rico  AGUADILLA   
30   Aguadilla          PR  Puerto Rico  AGUADILLA   
31   Aguadilla          PR  Puerto Rico  AGUADILLA   
32   Aguadilla          PR  Puerto Rico  AGUADILLA   
33   Aguadilla          PR  Puerto Rico  AGUADILLA   
34   Aguadilla          PR  Puerto Rico  AGUADILLA   
35   Aguadilla          PR  Puerto Rico  AGUADILLA   
36   Aguadilla          PR  Puerto Rico  AGUADILLA   
37   Aguadilla          PR  Puerto Rico  AGUADILLA   
38   Aguadilla          PR  Puerto Rico  AGUADILLA   
39   Aguadilla          PR  Puerto Rico  AGUADILLA   
40   Aguadilla          PR  Puerto Rico  AGUADILLA   
41   Aguadilla          PR  Puerto Rico  AGUADILLA   
42   Aguadilla          PR  Puerto Rico  AGUADILLA   
43   Aguadilla          PR  Puerto Rico  AGUADILLA   
44   Aguadilla          PR  Puerto Rico  AGUADILLA   
45     Maricao          PR  Puerto Rico    MARICAO   
46     Maricao          PR  Puerto Rico    MARICAO   
47      Anasco          PR  Puerto Rico     ANASCO   
48      Anasco          PR  Puerto Rico     ANASCO   
49      Anasco          PR  Puerto Rico     ANASCO   

                      City alias  k  
0       Internal Revenue Service  0  
1                     Holtsville  0  
2                URB San Joaquin  0  
3               Jard De Adjuntas  0  
4            Colinas Del Gigante  0  
5                       Adjuntas  0  
6           Comunidad Las Flores  0  
7         URB Isabel La Catolica  0  
8                 Alts De Aguada  0  
9                 Bo Guaniquilla  0  
10                        Aguada  0  
11                Ext Los Robles  0  
12                         Ramey  0  
13                     Aguadilla  0  
14                   Repto Lopez  0  
15               URB Maleza Gdns  0  
16                  URB Victoria  0  
17             Repto Tres Palmas  0  
18               Sect Las Villas  0  
19                    URB Garcia  0  
20                   Villa Linda  0  
21           Villa Universitaria  0  
22                 Bo Ceiba Baja  0  
23                 URB Borinquen  0  
24                 Villa Alegria  0  
25                  Vista Alegre  0  
26                URB San Carlos  0  
27                     Bda Caban  0  
28                  Ext El Prado  0  
29                   URB Esteves  0  
30                     URB Ramey  0  
31             Villas De Almeria  0  
3

In [18]:
import nltk
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('maxent_ne_chunker')
nltk.download('words')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\nelson.wang\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\nelson.wang\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     C:\Users\nelson.wang\AppData\Roaming\nltk_data...
[nltk_data]   Package maxent_ne_chunker is already up-to-date!
[nltk_data] Downloading package words to
[nltk_data]     C:\Users\nelson.wang\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


True

In [26]:
def Identification_Org(df_memo,df_tt):
    count,go=1,0
    con,org,none=[],[],[]
    df_memo["Organization"]=""
    city = list(df["City"].unique())
    city = [i.upper() for i in city] 
    
    def Preprocessing(i):
        i = re.sub("ACH CREDIT|ACH CONCENTRATION CREDIT|ACH DEBIT"\
                   "|ACH DEPOSIT|ACH DEP|ACH ELECTRONIC CREDIT|ACH ELECTRONIC DEBIT|ACH PAYMENT|ACHTRANS|AUTOMATIC WITHDRAWAL"\
                   "|BUSINESS TO BUSINESS|B/O|BNF=|CORPORATE ACH|DEBIT CARD PURCHASE|DIRECT DEPOSIT"\
                   "|EXTERNAL WITHDRAWAL|INTERNET TRF|MERCHANT PAYMENT|ORIG CO NAME|ORG="\
                   "|PAYMENT TO|POINT OF SALE DEBIT|POS DEBIT|POS MAC|POS PURCHASE|TRANSFER FROM|TRANSFER TO","AS ",i)
        
        i = re.sub("(?i)ACH PMT|ADJUSTMENT|AUTHORIZED|BUSINESS DEBIT"\
                   "|CHECKCARD|CCD|CKF|CO:|CRD|DBT|DDA|DEPOSIT"\
                   "|ELECTRONIC DEBIT|ELECTRONIC FUNDS|ELECTRONIC PAYMENT|ELECTRONIC PMT|ELECTRONIC DEPOSIT|ELECTRONIC WITHDRAWAL|ELECTRONIC TRANSACTION"\
                   "|FEDWIRE|FINANCIN  PAYMENT|FROM|INTL WIRE|INST XFER"\
                   "|ONLINE|OTHER DECREASE|POINT OF SALE|PURCHASE|PPD|P\.O\.S|RCVD|REAL TIME|RETURN|RECURRING PAYMENT|RFB|REF="\
                   "|SETTLEMENT|TRANSACTION|TYPE"\
                   "|WITHDRAWAL|WIRE/IN|WIRE/OUT|WIRE TRANS|WIRE TRANSFER|WIRELESS||WT FED|WWW|XFER","",i)

        i = re.sub(r"\\|'|-|\?|\!|&","",i) #Symbols
        i = re.sub("(?i)xx*xx|/|\**\*"," ",i)#Special conditions
        i = re.sub("[0-9]+"," ",i) #Number
        i = re.sub(r"\.|\bAUT\b|\bACH\b|\bON\b|\bCHECK\b|\bCARD\b|\bCOM\b|\bDEBIT\b|\bDATE\b|\bDES\b|\bDRAFT\b"\
                   r"|\bELECTRONIC\b|\bFEE\b|\bFEES\b|\bFOR\b|\bID\b|\bNA\b|\bORG\b|\bPOS\b|\bPIN\b|\bPMNT\b|\bPYMNTS\b|\bPUR\b|\bRECD\b|\bREF\b"\
                   r"|\bTRANS\b|\bTRAN\b|\bTRN\b|\bTO\b|\bVIA\b|\bVISA\b|\bVSA\b|\bWT\b|\bWEB\b|\bXX\b|XX\b"," ",i) #Exact same word
        i = re.sub("[\W]"," ",i)
        i = re.sub(' +', ' ',i)
        i = re.sub(r"\b[A-Z]\b","",i)
        return i
                
    blocklist=['AT','ACI','CA','CHEK','CHECK','CHIPS','COMMISSION','CO','CREDIT','DE','EDI',\
               'ENTRY','HCCLAIMPMT','ID','IN','INC','IND','INDN', 'LLC','NON','NY', 'OH','ORIG',\
                'PAYMENT','PAYMENTS','PYMT','PMT','QUICKBOOKS','QBOOKS','SAN','SENT','SETTLE','TIME','US', 'USA','WA', 'WITH','WIRE']
    #Keywords:    
    favlist=["ALLY","ADVANCE","ADVANCE AUTO","AMERICAN EXPRESS","AMAZON","AMZN","AMZ","APPLE","ATT","ATM",\
            "BEST BUY","BRP","BANKCD","BNKCD",\
            "CAPITAL ONE","CASH APP","CHASE","CREDIT ONE",\
            "DAVO","DOORDASH","DOLLAR",\
            "ELEVEN","GAS","GM FINANCIAL","GROCERY","HEB","HOME DEPOT","INTUIT",\
            "ITRIA","IRS","IN N OUT","JPM","MERCHANT BANKCD","MKTP","ONYX","OFFICE DEPOT","PAYPAL","PILOT","PETRO",\
            "SO CAL","SPEEDWAY","STRIPE","SQ","SQUARE","SUPERCENTER","STAPLES","TARGET","UBER","VENMO","VADER","VENTURE","VENTURES",\
            "WALMART","WM","WELLS FARGO","ZELLE"]
    
    #Entire name of the company:
    automobile=["CAPITAL ONE AUTO","CIRCLE K","DAT SOLUTIONS","MARATHON","MURPHY EXPRESS","OREILLY AUTO"]
    
    insurance=["AAA","AM INCOME","ANTHEM BLUE","CAPITAL PREMIUM","FIRST INSURANCE","GLOBE LIFE","HARTFORD",\
               "LIBERTY MUTUAL","NATIONAL GENERAL","PAYCHEX","PAYX","ROOT INSURANCE","STATE FARM","WESTGUARD"]
    
    def NLP_Processcing(sent):
        for chunk in nltk.ne_chunk(nltk.pos_tag(nltk.word_tokenize(sent))):
            if hasattr(chunk, 'label'):
                for c in chunk:
                    if c[0] not in blocklist and c[0] not in city and len(c[0])>1:
                        blank.append(c[0])
                        print(f"{chunk.label()} {c[0]}")
    
    
    
    
    for i in df_memo["Description"]:
        print(count)
        try:
            i = i.upper()
        except:
            i=str(i)
            i = "F"
        x,flag,blank,payment="",False,[],[]
        
        if re.search(r"(?i)(DEPT\s*OF)",i):
            flag=True
            try:
                try:
                    x = re.findall(r"(?i)(DEPT OF\s(...))",i)[0][0]
                except AttributeError:
                    x = re.findall(r"(?i)(DEPT OF\s(..))",i)[0][0]
                except:
                    x = re.findall(r"(?i)(DEPT OF\s(.))",i)[0][0]
                x = re.sub(r"[\W]","",x)
            except:
                x= re.findall(r"(DEPTOF(...))",i)[0][0]
            blank.append(x)
            
        elif  re.search(r"(?i)\bIRS\b",i):
            flag=True
            blank.append("IRS")  
            
            
        elif i[0:7]=="FEDWIRE":
            i =re.split(r"VIA: |B/O: |BNF=",i)
            for k in i:
                k = re.sub(" ","",k,1)
                k = Preprocessing(k)
                k = " AS "+k
                x+=k
            i = x
        
        elif re.search("ORIG CO NAME",i) and re.search("ORIG ID",i):
            flag=True
            i = re.search(r'ORIG CO NAME:(.*?)ORIG ID', i).group(1)
            blank.append(i)
            print(blank)
            
        elif re.search(r"\bINDN\b",i):
            i = re.findall(r"(.*?)\bINDN\b",i)[0]
            
        elif re.search(r"\bIND\b",i):
            i = re.findall(r"(.*?)\bIND\b",i)[0]
        
        #Payment Processor
        '''elif re.search(r"(?i)\bINTUIT\b|\bMERCHANT BANKCD\b|\bSQ\b|\bSQUARE\b",i):
            print("Found Payment Processor")
            print(i)
            payment.append(re.findall(r"(?i)\bINTUIT\b|\bMERCHANT BANKCD\b|\bSQ\b|\bSQUARE\b",i)[0])
            i = re.sub(r"(?i)\bINTUIT\b|\bMERCHANT BANKCD\b|\bSQ\b|\bSQUARE\b","",i)
            print("After:")
            i = Preprocessing(i)
            print(i)
            print(payment)'''

        i = Preprocessing(i)

        if len(re.findall(r"\bAS\b",i[0:7]))>1: #Make sure only has one "AS" at the begining
            i = re.sub(r"\bAS\b","",i,1)
        
        if bool(i) == False or i.isspace() == True: #To Avoid the situation like nothing or only white space in the sentence
            i+="F"

        print(i)
#NLP Process:
        if flag==True:
            n = 0
            for j in blank:
                k = re.sub("[\s]","",j)
                if re.search(r"[\W]",k):
                    print("Before")
                    print(blank)
                    blank[n] = re.sub("XX*XX"," ",j)
                    blank[n] = re.sub("[\W]"," ",blank[n])
                    blank[n] = re.sub(' +', ' ',blank[n])
                    blank[n] = re.sub("[0-9]+"," ",blank[n])
                    blank[n] = blank[n].rstrip()
                    n+=1
                    print("Found non-Char")
                    print(blank)
                    

        else:
            
            for sent in nltk.sent_tokenize(i):
                x=""        
                NLP_Processcing(sent)

                #To avoid the unidentification of the frently showed company:

                for j in favlist:
                    if re.search(r"\b"+j+r"\b",sent):
                        blank.append(j)
                for j in automobile:
                    if re.search(r"\b"+j,sent):
                        blank.append(j)
                for j in insurance:
                    if re.search(r"\b"+j,sent):
                        blank.append(j)
                
                if len(blank) ==0:
                    print(sent)
                    sent = re.sub(r"\bAS\b","",sent,1)
                    sent = re.sub(r"\bSAN\b"," ",sent)
                    sent= sent.strip()
                    sent=re.sub(" ","",sent,1)
                    sent = re.sub(r"\bLX\b|\bXX\b"," ",sent)
                    sent= "AS " + sent
                    print(sent)
                    NLP_Processcing(sent)

                #Make sure split all the words
        print("First Process:")
        print(blank)

        word = nltk.word_tokenize(i)
        string = ' '.join(blank)
        x = np.array(string.split())
        y = np.unique(x, return_index=True)[0]
        newlist = y.tolist()
        new=[]
        
        #Correct order of name to be displayed
        for j in word:
            if j in newlist:
                new.append(j)
        if len(new)==0:
            new = blank
        
        elif len(new)>3:
            new = new[0:5]
            
        #Last filter
        last=[]
        orgtype=["LLC","INC","DE","CA","IN"]
        for j in new:
            if j not in orgtype:
                last.append(j)
        new=last
            
        new = np.array(new)
        y = np.unique(new, return_index=True)[1]
        new = ([new[index] for index in sorted(y)])
        new = payment+new
        print("Last Filter")
        print(new)
        
        new = ' '.join(new) #Convert list to string
        df_memo["Organization"].iloc[go] = new
        print(f"Index: {go}")
        print(df_memo["Organization"].iloc[go] )
        go+=1
        org.append(blank)

        #Find those words are frequently unidentified
        words = pd.DataFrame(nltk.word_tokenize(i))
        tt = words[~words[0].isin(blank)]
        for j in tt[0]:
            con.append(j)

        print("\n")
        count+=1


    #Showing the Performance
    ct=0
    for i in org:
        if len(i)>0:
            ct+=1
    print(f"Found:\t{ct}")
    print(f"Total Transactions:\t{len(org)}")
     
    def Unidentified_Analysis(df_tt):
        #Unimportant Words for analysis:
        neg = ['AC', 'ACTION', 'ADD', 'AM', 'AMZ', 'AND', 'ANGELES', 'APP', 'AT', 'AUTO', 'AVE', 'AZUS',\
               'B', 'BACK', 'BEST', 'BI', 'BIL', 'BILL', 'BILLWA', 'BP', 'BR', 'BRJPM', 'BRP', 'BUY',\
               'CAR', 'CASH', 'CAÂ', 'CC', 'CHECKING', 'CHK', 'CIRCLE', 'CITY', 'CK', 'CKCD', 'CKCD', 'CO', 'CONF', 'CONFIRMATION', 'CR', 'CREDIT',\
               'DATE', 'DD', 'DEBIT', 'DEP', 'DEPOSITXX', 'DES', 'DESC', 'DESCR', 'DIRECT',\
               'EBAY', 'EDI', 'EED', 'EL', 'ENDING', 'ENTRY', 'EPAYMENT',\
               'FED', 'FEE', 'FER', 'FOODS', 'FOR', 'FORT', 'FRANCISCOCA', 'FROM', 'FUEL', 'H', 'HAL', 'HELP', 'HOME',\
               'IB', 'ID', 'IMAGE', 'INC', 'IND', 'INDN', 'INFINITELOOP', 'INFO', 'INST', 'INVESTMENTS', 'INVOICES', 'IT',\
               'JANICE', 'JOSE', 'LAS', 'LITTLE', 'LL', 'LLC', 'M', 'MERCH', 'MF', 'MLT', 'MM', 'MU', 'MY', 'NAME', 'NBR', 'NET',\
               'O', 'OAK', 'OF', 'OFFICE', 'ONLINE', 'ORIG', 'OUT', 'OVER',\
               'PAY', 'PAYMENT', 'PAYMNTSEC', 'PM', 'PMNT', 'PMT', 'POS', 'POSTING', 'PP', 'PUR', 'PYMT', 'QT',\
               'RCVD', 'RD', 'RECD', 'RECURRING', 'REF', 'REFERENCE', 'RX',\
               'S', 'SAN', 'SEC', 'SEQ', 'SERVICE', 'SERVICES', 'SETLMT', 'SETTLEMENTSEC', 'SHOP', 'SP', 'SRF', 'SS',\
               'ST', 'STATION', 'STORE', 'STORES', 'SUP', 'SUPER', 'SUPERC', 'TC', 'TERMINAL', 'TH', 'THE', 'THORNTONS',\
               'TIRE', 'TN', 'TO', 'TR', 'TRACE', 'TRAN', 'TRUCK', 'TRUCKING', 'TXÂ', 'US', 'USA', 'VEGAS', 'VISA',\
               'WAUS', 'WEB', 'WFBPVOTL', 'WHSE', 'WITH', 'WM', 'WT', 'X', 'XFER', 'XT', 'XX', 'YADON']
        
        df_tt = df_tt[df_tt["count"]>10]
        for i,j in df_tt.iterrows():
            if len(j[0])<2:               
                df_tt.drop([i],inplace=True) 
            
            elif re.search(r"[\W]",j[0]):
                df_tt.drop([i],inplace=True)
            
            for ss in df["State short"].unique():
                if j[0]==ss:
                    df_tt.drop([i],inplace=True)
            for ss in city:
                if j[0]==ss:
                    df_tt.drop([i],inplace=True)
                    
        df_tt = df_tt[~df_tt["Name"].isin(neg)].sort_values("count",ascending=False)
        return df_tt
        
    
    df_tt = pd.DataFrame(con, columns=["Name"])
    df_tt = (df_tt.groupby(["Name"]).agg({"Name":["count"]}))
    df_tt.columns = df_tt.columns.droplevel()
    df_tt.reset_index(inplace=True)
    df_tt = Unidentified_Analysis(df_tt)
    
    return df_memo,df_tt

# NLP_Report-1013

In [21]:
df_memo_ach = pd.read_excel("NLP_Report-1013.xlsx", sheet_name="ACH")
df_memo_PA= pd.read_excel("NLP_Report-1013.xlsx", sheet_name="PurchaseAuth")
df_memo_CK=pd.read_excel("NLP_Report-1013.xlsx", sheet_name="Checkcard")
df_memo_DS=pd.read_excel("NLP_Report-1013.xlsx", sheet_name="Debt")
df_memo_LI=pd.read_excel("NLP_Report-1013.xlsx", sheet_name="Liability") 
df_memo_AUTO=pd.read_excel("NLP_Report-1013.xlsx", sheet_name="Auto")
df_memo_RT=pd.read_excel("NLP_Report-1013.xlsx", sheet_name="Retail")
df_auto1300=pd.read_excel("NLP_Report-1013.xlsx", sheet_name = "Auto1300")
df_retail3600=pd.read_excel("NLP_Report-1013.xlsx", sheet_name="Retail3600")
df_rand2500=pd.read_excel("NLP_Report-1013.xlsx",sheet_name="Random2500")
df_tt = pd.DataFrame()

In [27]:
df_memo_ach,df_tt = Identification_Org(df_memo_ach,df_tt)
df_memo_PA,df_tt = Identification_Org(df_memo_PA,df_tt)
df_memo_CK,df_tt = Identification_Org(df_memo_CK,df_tt)
df_memo_DS,df_tt = Identification_Org(df_memo_DS,df_tt)
df_memo_LI,df_tt = Identification_Org(df_memo_LI,df_tt)
df_memo_AUTO,df_tt = Identification_Org(df_memo_AUTO,df_tt)
df_memo_RT,df_tt = Identification_Org(df_memo_RT,df_tt)
df_auto1300,df_tt = Identification_Org(df_auto1300,df_tt)
df_retail3600,df_tt = Identification_Org(df_retail3600,df_tt)
df_rand2500,df_tt = Identification_Org(df_rand2500,df_tt)

1
AS NONREF 
ORGANIZATION NONREF
First Process:
['NONREF']
Last Filter
['NONREF']
Index: 0
NONREF


2
AS NONREF 
ORGANIZATION NONREF
First Process:
['NONREF']
Last Filter
['NONREF']
Index: 1
NONREF


3
AS NONREF 
ORGANIZATION NONREF
First Process:
['NONREF']
Last Filter
['NONREF']
Index: 2
NONREF


4
AS NONREF 
ORGANIZATION NONREF
First Process:
['NONREF']
Last Filter
['NONREF']
Index: 3
NONREF


5
AS NONREF 
ORGANIZATION NONREF
First Process:
['NONREF']
Last Filter
['NONREF']
Index: 4
NONREF


6
AS BJ HOLDINGS FTB BRP HOLDINGS 
ORGANIZATION BJ
ORGANIZATION HOLDINGS
First Process:
['BJ', 'HOLDINGS', 'BRP']
Last Filter
['BJ', 'HOLDINGS', 'BRP']
Index: 5
BJ HOLDINGS BRP


7
AS BJ HOLDINGS INVOICE BRP INVESTMENTS BJ 
ORGANIZATION BJ
ORGANIZATION HOLDINGS
First Process:
['BJ', 'HOLDINGS', 'BRP']
Last Filter
['BJ', 'HOLDINGS', 'BRP']
Index: 6
BJ HOLDINGS BRP


8
AS  SQUARE INC   
ORGANIZATION SQUARE
First Process:
['SQUARE', 'SQUARE']
Last Filter
['SQUARE']
Index: 7
SQUARE


9
AS  SQUARE IN

In [28]:
with pd.ExcelWriter("testing.xlsx") as writer:
    df_memo_ach.to_excel(writer, sheet_name="ACH", index=True)
    df_memo_PA.to_excel(writer, sheet_name="PurchaseAuth", index=True)
    df_memo_CK.to_excel(writer, sheet_name="Checkcard", index=True)
    df_memo_DS.to_excel(writer, sheet_name="Debt", index=True)
    df_memo_LI.to_excel(writer, sheet_name="Liability", index=True) 
    df_memo_AUTO.to_excel(writer, sheet_name="Auto", index=True)
    df_memo_RT.to_excel(writer, sheet_name="Retail", index=True)
    df_auto1300.to_excel(writer, sheet_name = "Auto1300", index=False)
    df_retail3600.to_excel(writer, sheet_name="Retail3600", index = False)
    df_rand2500.to_excel(writer,sheet_name="Random2500", index=False)

# Automobile

In [170]:
df_22q2 = df_22q2[df_22q2['Classification'].notna()]

In [174]:
df_auto = df_22q2.loc[df_22q2.Classification.str.contains('Automotive Supplies/Services ')]

In [175]:
df_auto.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 278843 entries, 4 to 7195980
Data columns (total 12 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   Unnamed: 0        278843 non-null  int64  
 1   Unnamed: 0.1      278843 non-null  int64  
 2   Lead Id           278843 non-null  int64  
 3   account_number    278147 non-null  object 
 4   post_date         278843 non-null  object 
 5   description       278843 non-null  object 
 6   transaction_type  278843 non-null  object 
 7   amount            278843 non-null  float64
 8   running_balance   278843 non-null  float64
 9   Classification    278843 non-null  object 
 10  Source_class      0 non-null       object 
 11  Source            1635 non-null    object 
dtypes: float64(2), int64(3), object(7)
memory usage: 27.7+ MB


In [465]:
df_auto_s = pd.read_excel("NLP_Report-AutoInsPay.xlsx",sheet_name="Auto3000")

In [519]:
%%time
df_tt_auto=pd.DataFrame()
df_auto_s,df_tt_auto = Identification_Org(df_auto_s,df_tt_auto)

1
ACCOUNT NUMBER AUTO OVERDRAFT TRANSFER
ORGANIZATION ACCOUNT
First Process:
['ACCOUNT']
Last Filter
['ACCOUNT']
Index: 0
ACCOUNT


2
ACCOUNT NUMBER AUTO OVERDRAFT TRANSFER
ORGANIZATION ACCOUNT
First Process:
['ACCOUNT']
Last Filter
['ACCOUNT']
Index: 1
ACCOUNT


3
ACCOUNT NUMBER AUTO OVERDRAFT TRANSFER
ORGANIZATION ACCOUNT
First Process:
['ACCOUNT']
Last Filter
['ACCOUNT']
Index: 2
ACCOUNT


4
ACCOUNT NUMBER AUTO OVERDRAFT TRANSFER
ORGANIZATION ACCOUNT
First Process:
['ACCOUNT']
Last Filter
['ACCOUNT']
Index: 3
ACCOUNT


5
 ACE TRUCK PARKING FL  
ORGANIZATION ACE
ORGANIZATION TRUCK
First Process:
['ACE', 'TRUCK']
Last Filter
['ACE', 'TRUCK']
Index: 4
ACE TRUCK


6
['ACV CAPITAL LLC        ']
ACV CAPITAL LLC 
First Process:
['ACV CAPITAL LLC        ']
Last Filter
['ACV', 'CAPITAL']
Index: 5
ACV CAPITAL


7
ADAM OIL LLC PONTIAC MI 
ORGANIZATION ADAM
ORGANIZATION OIL
First Process:
['ADAM', 'OIL']
Last Filter
['ADAM', 'OIL']
Index: 6
ADAM OIL


8
 ADVANCE AUTO PARTS KISSIMMEE FL 
ORGANIZ

C:\Users\nelson.wang\Anaconda3\lib\site-packages\pandas\core\indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


ORGANIZATION SIGNED
ORGANIZATION ADVANCE
ORGANIZATION PARTS
First Process:
['SIGNED', 'ADVANCE', 'PARTS', 'ADVANCE', 'ADVANCE AUTO']
Last Filter
['SIGNED', 'ADVANCE', 'AUTO', 'PARTS']
Index: 33
SIGNED ADVANCE AUTO PARTS


35
ADVANCE AUTO PARTS  LITTLE ROCK AR 
ORGANIZATION ADVANCE
ORGANIZATION AUTO
ORGANIZATION PARTS
First Process:
['ADVANCE', 'AUTO', 'PARTS', 'ADVANCE', 'ADVANCE AUTO']
Last Filter
['ADVANCE', 'AUTO', 'PARTS']
Index: 34
ADVANCE AUTO PARTS


36
 ADVANCE AUTO PA COLORADO SPRI CO  
ORGANIZATION AUTO
First Process:
['AUTO', 'ADVANCE', 'ADVANCE AUTO']
Last Filter
['ADVANCE', 'AUTO']
Index: 35
ADVANCE AUTO


37
 PURCH ADVANCE AUTO PAR SPRUCE PINE NC 
ORGANIZATION PAR
First Process:
['PAR', 'ADVANCE', 'ADVANCE AUTO']
Last Filter
['ADVANCE', 'AUTO', 'PAR']
Index: 36
ADVANCE AUTO PAR


38
ADVANCE AUTO  FONDREN RD HOUSTON TX
ORGANIZATION AUTO
First Process:
['AUTO', 'ADVANCE', 'ADVANCE AUTO']
Last Filter
['ADVANCE', 'AUTO']
Index: 37
ADVANCE AUTO


39
 ADVANCE AUTO PA GULFPORT F

C:\Users\nelson.wang\Anaconda3\lib\site-packages\pandas\core\frame.py:4906: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


Wall time: 19 s


In [329]:
df_auto_s.to_excel("testing.xlsx")

# Insurance

In [177]:
df_ins = df_22q2.loc[df_22q2.Classification.str.contains('Insurance ')]

In [257]:
df_ins.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 74823 entries, 131 to 7195696
Data columns (total 12 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Unnamed: 0        74823 non-null  int64  
 1   Unnamed: 0.1      74823 non-null  int64  
 2   Lead Id           74823 non-null  int64  
 3   account_number    74704 non-null  object 
 4   post_date         74823 non-null  object 
 5   description       74823 non-null  object 
 6   transaction_type  74823 non-null  object 
 7   amount            74823 non-null  float64
 8   running_balance   74823 non-null  float64
 9   Classification    74823 non-null  object 
 10  Source_class      0 non-null      object 
 11  Source            432 non-null    object 
dtypes: float64(2), int64(3), object(7)
memory usage: 7.4+ MB


In [180]:
df_ins_s = df_ins.sample(n=3000)

In [388]:
df_ins_s = pd.read_excel("NLP_Report-AutoInsPay.xlsx", sheet_name="Ins3000")

FileNotFoundError: [Errno 2] No such file or directory: 'Temporary-FurtherTesting.xlsx'

In [418]:
%%time
df_tt_ins=pd.DataFrame()
df_ins_s,df_tt_ins = Identification_Org(df_ins_s,df_tt_auto)

1
NATIONWIDE EDI ID NBP 
ORGANIZATION NATIONWIDE
First Process:
['NATIONWIDE']
Last Filter
['NATIONWIDE']
Index: 0
NATIONWIDE


2
ZELLE PAYMENT BIG TRUCK INSURANCE LLC 
ORGANIZATION ZELLE
First Process:
['ZELLE', 'ZELLE']
Last Filter
['ZELLE']
Index: 1
ZELLE


3
  AS DELTA BRIDGE FUN DELTA BRID MAY DEB ALLCITYINSURANCEAGENC
  AS DELTA BRIDGE FUN DELTA BRID MAY DEB ALLCITYINSURANCEAGENC
AS DELTABRIDGE FUN DELTA BRID MAY DEB ALLCITYINSURANCEAGENC
ORGANIZATION DELTABRIDGE
First Process:
['DELTABRIDGE']
Last Filter
['DELTABRIDGE']
Index: 2
DELTABRIDGE


4
AS FARM BUREAU PROPERTY CASUALTY INSURANCE
ORGANIZATION FARM
First Process:
['FARM']
Last Filter
['FARM']
Index: 3
FARM


5
['LIBERTY MUTUAL ']
LIBERTY MUTUAL 
First Process:
['LIBERTY MUTUAL ']
Last Filter
['LIBERTY', 'MUTUAL']
Index: 4
LIBERTY MUTUAL


6
COMBINED INS INS PREM   MARIA  CURY
ORGANIZATION COMBINED
ORGANIZATION INS
First Process:
['COMBINED', 'INS']
Last Filter
['COMBINED', 'INS']
Index: 5
COMBINED INS


7
['ACCENDO INSURAN

In [419]:
df_ins_s.to_excel("testing2.xlsx")

In [191]:
with pd.ExcelWriter("testing.xlsx") as writer:
    df_auto_s.to_excel(writer, sheet_name="Auto3000",index=True)
    df_ins_s.to_excel(writer, sheet_name="Ins3000",index=True)

# Tax & Gov

In [290]:
df_taxgov = pd.read_excel("NLP_Report-Tax&Gov.xlsx")

In [295]:
%%time
df_tt_tg=pd.DataFrame()
df_taxgov,df_tt_tg = Identification_Org(df_taxgov,df_tt_tg)

1
IRS TREAS CHILDCTC ID INDN BADR MAMDOUUH CO ID 
Final
['IRS']
['IRS']
Index: 0
IRS


2
 MN DEPT OF DEED
Final
['DEPTOFDEE']
['DEPTOFDEE']
Index: 1
DEPTOFDEE


3
IRS TREAS CHILDCTC ID INDN DEANGELIS DAVID J CO ID 
Final
['IRS']
['IRS']
Index: 2
IRS


4
LOUISIANA DEPT OF REV LA 
Final
['DEPTOFREV']
['DEPTOFREV']
Index: 3
DEPTOFREV


5
 IRS TREAS 
Final
['IRS']
['IRS']
Index: 4
IRS


6
AS IRS USATAXPYMT USED CAR ENTERPRISE LL
Final
['IRS']
['IRS']
Index: 5
IRS


7
IRS USATAXPYMT ID INDN CONNECT INCOR CO ID 
Final
['IRS']
['IRS']
Index: 6
IRS


8
FL DEPT OF REVE CHILDSUPP ID INDN DANIELLE L WASHINGTON CO ID 
Final
['DEPTOFREV']
['DEPTOFREV']
Index: 7
DEPTOFREV


9
 IRS USATAXPYMT 
Final
['IRS']
['IRS']
Index: 8
IRS


10
MN DEPT OF DEED UI BENEFIT ID INDN FARRENKOPF SHAWN L CO ID 
Final
['DEPTOFDEE']
['DEPTOFDEE']
Index: 9
DEPTOFDEE


11
IRS USATAXPYMT ID INDN ND CHANCE TRADING INC CO ID 
Final
['IRS']
['IRS']
Index: 10
IRS


12
IRS TREAS TAX REF KEY YASMIN K
Final
['IRS']
['IRS']
Index: 

C:\Users\nelson.wang\Anaconda3\lib\site-packages\pandas\core\indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)




56
IRS TREAS CHILDCTC KUKSENKO VLADIMIR D
Final
['IRS']
['IRS']
Index: 55
IRS


57
IRS TREAS CHILDCTC ID INDN JOHNSON LATANIA T CO ID 
Final
['IRS']
['IRS']
Index: 56
IRS


58
IRS TREAS CHILDCTC ID INDN CEJA DANIEL YARI T CO ID 
Final
['IRS']
['IRS']
Index: 57
IRS


59
IRS TREAS CHILDCTC PORTER TATYANA C
Final
['IRS']
['IRS']
Index: 58
IRS


60
AS IL DEPT OF REVEN ORIG ID DESC CO ENTRY DESCR EDI PYMNTSSEC TRACE EED IND ID IND NAME FAISAL DOSSA TC
Final
['DEPTOFREV']
['DEPTOFREV']
Index: 59
DEPTOFREV


61
IRS TREAS CHILDCTC ID 
Final
['IRS']
['IRS']
Index: 60
IRS


62
MN DEPT OF DEED UI BENEFIT CHALFIN LESLIE M
Final
['DEPTOFDEE']
['DEPTOFDEE']
Index: 61
DEPTOFDEE


63
AS IRS ORIG ID DESC CO ENTRY DESCR USATAXPYMTSEC TRACE EED IND ID IND NAME TEXAS PUBLIC SAFETY TC
Final
['IRS']
['IRS']
Index: 62
IRS


64
CORPORATE IRS USATAXPYMT
Final
['IRS']
['IRS']
Index: 63
IRS


65
 AS DEPT OF BUS BILLERPAY 
Final
['DEPTOFBUS']
['DEPTOFBUS']
Index: 64
DEPTOFBUS


66
IRS USATAXPYMT FREDERICK A TAI

C:\Users\nelson.wang\Anaconda3\lib\site-packages\pandas\core\frame.py:4906: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


Wall time: 6.74 s


In [296]:
df_tt_tg

Name  count
1155          TREAS    392
1175     USATAXPYMT    349
195        CHILDCTC    276
293            DEPT    127
1177  USATAXPYMTSEC    101
1098            TAX     51
1168             UI     35
951           REVEN     33
949             REV     31
659           LABOR     28
1166            TXP     24
243            CORP     23
1141          TOTAL     20
934             REG     20
1048      SOLUTIONS     18
1107           TECH     16
915       PYMNTSSEC     16
311             DIR     16
466           GROUP     14
285            DEED     13
196     CHILDCTCSEC     13
111         BENEFIT     11
914          PYMNTS     11
245       CORPORATE     11
78              ATM     11

In [297]:
df_taxgov.to_excel("NLP_Report-Tax&Gov.xlsx")

# Payment Processor

In [36]:
df_pay= pd.read_excel("NLP_Report-payment.xlsx",sheet_name="Payment")

In [37]:
%%time
df_tt_pay=pd.DataFrame()
df_pay,df_tt_pay= Identification_Org(df_pay,df_tt_pay)

1
AS INTUIT FINANCIN PAYMENT BALLMAN CONSTRUCTION 
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTUIT']
Index: 0
INTUIT


2
AS INTUIT FINANCIN PAYMENT SOCAL RACING INDUSTRIE
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTUIT']
Index: 1
INTUIT


3
AS INTUIT FEE UP NORTH UP KEEP LLC
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTUIT']
Index: 2
INTUIT


4
AS INTUIT FEE HARRISON ZAHOR VA ENTE
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTUIT']
Index: 3
INTUIT


5
AS INTUIT FEE SHELBY PARK MARKETING
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTUIT']
Index: 4
INTUIT


6
AS INTUIT FEE HELP ME RONDA LLC
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTUIT']
Index: 5
INTUIT


7
AS INTUIT FEE VICTORY HOSPITALITY 
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTUIT']
Index: 6
INTUIT


8
AS INTUIT FEE MICRO RENAISSANCE TECH
ORGANIZATION INTUIT
First Process:
['INTUIT']
Last Filter
['INTU

C:\Users\nelson.wang\Anaconda3\lib\site-packages\pandas\core\frame.py:4906: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


Wall time: 2.53 s


In [38]:
df_pay.to_excel("testing.xlsx")